In [2]:
import cv2
import mediapipe as mp
import numpy as np
import os
import copy
import itertools
#vftgbyhunjmi

In [56]:
dataset = "D:\Dataset"

classList = ['Actor', 'Adult', 'Animal', 'Artist', 'Attack', 'Author', 'Baby', 'Bad', 'Bag', 'Ball', 'Bank', 'Bathroom', 'Bed', 'Bedroom', 'Bicycle', 'Big', 'Bill', 'Bird', 'Boat', 'Book', 'Box', 'Boy', 'Brother', 'Bus', 'Car', 'Card', 'Cat', 'Chair', 'Child', 'City', 'Cold', 'Cool', 'Court', 'Cow', 'Crowd', 'Daughter', 'Death', 'Dirty', 'Doctor', 'Dog', 'Door', 'Dream', 'Dry', 'Election', 'Energy', 'Ex. Monsoon', 'Exercise', 'Expensive', 'Fall', 'Family', 'Famous', 'Fast', 'Father', 'Female', 'Fish', 'Flat', 'Friend', 'Gift', 'Girl', 'God', 'Good', 'Grandfather', 'Grandmother', 'Ground', 'Gun', 'Happy', 'Hard', 'He', 'Healthy', 'Heavy', 'High', 'Horse', 'Hospital', 'Hot', 'House', 'Husband', 'I', 'India', 'It', 'Job', 'Key', 'King', 'Kitchen', 'Lawyer', 'Letter', 'Library', 'Light', 'Location', 'Lock', 'Long', 'Loose', 'Loud', 'Low', 'Male', 'Man', 'Manager', 'Market', 'Marriage', 'Mean', 'Medicine', 'Money', 'Mother', 'Mouse', 'Narrow', 'Neighbour', 'New', 'Newspaper', 'Nice', 'Office', 'Old', 'Page', 'Paint', 'Paper', 'Parent', 'Park', 'Patient', 'Peace', 'Pen', 'Pencil', 'Photograph', 'Plane', 'Player', 'Police', 'Poor', 'President', 'Price', 'Priest', 'Queen', 'Quiet', 'Race (ethnicity)', 'Religion', 'Reporter', 'Restaurant', 'Rich', 'Ring', 'Sad', 'School', 'Science', 'Season', 'Secretary', 'Shallow', 'She', 'Shop', 'Short', 'Sick', 'Sign', 'Sister', 'Slow', 'Small', 'Soap', 'Soft', 'Soldier', 'Son', 'Sport', 'Spring', 'Street or Road', 'Strong', 'Student', 'Summer', 'Table', 'Tall', 'Teacher', 'Team', 'Technology', 'Telephone', 'Temple', 'They', 'Thick', 'Thin', 'Tight', 'Tool', 'Train', 'Train Station', 'Train ticket', 'Transportation', 'Truck', 'Ugly', 'University', 'Waiter', 'War', 'Warm', 'We', 'Weak', 'Wet', 'Wide', 'Wife', 'Window', 'Winter', 'Woman', 'you', 'You (plural)', 'Young'] 
print(len(classList))

192


In [53]:
hands = mp.solutions.hands.Hands(static_image_mode=False, max_num_hands=2, min_detection_confidence=0.5, min_tracking_confidence=0.5)
sequenceLength = 30

In [48]:
def normalizeCoordinates(coords):
    
    baseX = 0
    baseY = 0

    for i, val in enumerate(coords):
        if i == 0:
            baseX = val[0]
            baseY = val[1]

        coords[i][0] = coords[i][0] - baseX
        coords[i][1] = coords[i][1] - baseY 

    coords = list(itertools.chain.from_iterable(coords))

    maxVal = max(list(map(abs, coords)))

    def normalize_(n):
        return n / maxVal

    coords = list(map(normalize_, coords))

    return coords

In [49]:
def skeletonExtraction(path):

    left = []
    right = []
    cap = cv2.VideoCapture(path)

    while True:
        success, img = cap.read()

        if(success == False):

            cap.release()
            break
        
        imgRGB = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
        results = hands.process(imgRGB)
        
        hLeft = None
        hRight = None

        if(results.multi_hand_landmarks):
            for idx, handLms in enumerate(results.multi_hand_landmarks):
                
                hand = []
                for id, lm in enumerate(handLms.landmark):
                    h, w, c = img.shape
                    cx, cy = int(lm.x *w), int(lm.y*h)
                    hand.append([cx, cy])

                label = results.multi_handedness[idx].classification[0].label
                

                if(label == 'Left'):
                    hLeft = normalizeCoordinates(hand)
                elif(label == 'Right'):
                    hRight = normalizeCoordinates(hand)
        
        if(hLeft != None):
            left.append(hLeft)
        if(hRight != None):
            right.append(hRight)
    
    countLeft = len(left)
    countRight = len(right)
    windowLeft = max(countLeft/sequenceLength, 1)
    windowRight = max(countRight/sequenceLength, 1)

    finalFeatures = []

    if countLeft < sequenceLength or countRight < sequenceLength:
        return []


    for i in range(0, sequenceLength):
        
        finalFeatures.append(left[int(i * windowLeft)] + right[int(i * windowRight)])

    return np.asarray(finalFeatures)

In [15]:
def createDataset():

    features = []
    labels = []
    paths = []
    
    for index, name in enumerate(classList):
        filesList = os.listdir(os.path.join(dataset, name))

        for i in filesList:

            path = os.path.join(dataset, name, i)

            extractedFeatures = skeletonExtraction(path)

            if(len(extractedFeatures) == sequenceLength):
                features.append(extractedFeatures)
                labels.append(index)
                paths.append(path)
    
    features = np.asarray(features)
    labels = np.array(labels)

    return features, labels, paths

In [13]:
features, labels, paths = createDataset()

20 44 20 2.2 1.0 D:\Dataset\Actor\MVI_4516.MOV
[[0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Right'], [1, 'Left'], [0, 'Right'], [1, 'Left'], [0, 'Right'], [1, 'Left'], [0, 'Right'], [0, 'Left'], [1, 'Right'], [0, 'Left'], [1, 'Right'], [0, 'Right'], [0, 'Left'], [0, 'Left'], [1, 'Right'], [0, 'Left'], [0, 'Left'], [0, 'Right'], [0, 'Right'], [0, 'Right'], [0, 'Left'], [1, 'Right'], [0, 'Left'], [1, 'Right'], [0, 'Left'], [0, 'Right'], [0, 'Right'], [0, 'Left'], [1, 'Right'], [0, 'Left'], [1, 'Right'], [0, 'Left'], [1, 'Right'], [0, 'Left'], [1, 'Right'], [0, 'Left'], [1, 'Right'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left'], [0, 'Left']]
0 0
2 1
4 2
6 3
8 4
11 5
13 6
15 7
17 8
19 9
22 10
24 11
26 12
28 13
30 14
33 15
35 16
37 17
39 18
4

In [3]:
import pickle
from sklearn.model_selection import train_test_split
from keras.utils import to_categorical

In [3]:
featuresFile = open('features', 'rb')
labelsFile = open('labels', 'rb')
pathsFile = open('paths', 'rb')
features = pickle.load(featuresFile)
labels = pickle.load(labelsFile)
paths = pickle.load(pathsFile)
featuresFile.close()
labelsFile.close()
pathsFile.close()


In [4]:
encodedLabels = to_categorical(labels)

In [41]:
x_train, x_test, y_train, y_test = train_test_split(features, encodedLabels, test_size=0.01, random_state=69)


In [14]:
x_train.shape

(2368, 20, 126)

In [1]:
import tensorflow as tf
from keras import Sequential
from keras.layers import Dense, Dropout, LSTM, Activation, BatchNormalization

In [42]:
model = Sequential()
model.add(LSTM(128, return_sequences = True, input_shape = (30, 84)))
model.add(Activation('relu'))
model.add(Dropout(0.2))

model.add(LSTM(256))
model.add(Activation('relu'))
model.add(Dropout(0.2))

model.add(Dense(256))
model.add(Activation('relu'))
model.add(Dropout(0.2))
model.add(BatchNormalization())
model.add(Dense(193, activation='softmax'))

model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

In [21]:
from keras.callbacks import EarlyStopping

In [43]:
earlyStopping = EarlyStopping(monitor='val_loss', patience=10, mode='min', restore_best_weights=True)
model.fit(x = x_train, y = y_train, epochs=250, validation_split = 0.2)

Epoch 1/250
64/64 [==============================] - 14s 157ms/step - loss: 5.1641 - accuracy: 0.0207 - val_loss: 5.1322 - val_accuracy: 0.0473
Epoch 2/250
64/64 [==============================] - 9s 147ms/step - loss: 4.3809 - accuracy: 0.0760 - val_loss: 4.8097 - val_accuracy: 0.0986
Epoch 3/250
64/64 [==============================] - 9s 144ms/step - loss: 3.7528 - accuracy: 0.1348 - val_loss: 4.2949 - val_accuracy: 0.1479
Epoch 4/250
64/64 [==============================] - 9s 147ms/step - loss: 3.2433 - accuracy: 0.2044 - val_loss: 3.5832 - val_accuracy: 0.2485
Epoch 5/250
64/64 [==============================] - 9s 146ms/step - loss: 2.7483 - accuracy: 0.2919 - val_loss: 2.9374 - val_accuracy: 0.3333
Epoch 6/250
64/64 [==============================] - 9s 148ms/step - loss: 2.3409 - accuracy: 0.3901 - val_loss: 2.5381 - val_accuracy: 0.3669
Epoch 7/250
64/64 [==============================] - 9s 148ms/step - loss: 2.0757 - accuracy: 0.4444 - val_loss: 2.0660 - val_accuracy: 0.467

In [44]:
modelEvaluate = model.evaluate(x_test, y_test)

1/1 [==============================] - 3s 3s/step - loss: 0.0842 - accuracy: 0.9615


In [45]:
model.save_weights("modelskeleton8.h5")
modelJSON = model.to_json()
with open('modelskeleton8.json', 'w') as jsonFile:
    jsonFile.write(modelJSON)

model 7 used 0.15 test train and 0.15 train validation split
model 8 used 0.01 test train and 0.2 train validation split

In [46]:
def inputProcessing(path):
    features = skeletonExtraction(path)
    temp = [features]

    return np.asarray(temp)

In [69]:
features = inputProcessing("B:\PESU Labs\Capstone\ISL Translation\Demo\WhatsApp Video 2022-12-01 at 5.13.05 PM.mp4")
output = model.predict(features)
label = classList[np.argmax(output)]
print(label)

1/1 [==============================] - 0s 22ms/step
Light


In [4]:
import keras

In [5]:
jsonFile = open('modelskeleton8.json', 'r')
loadedModel = jsonFile.read()
loadedModel = keras.models.model_from_json(loadedModel)
loadedModel.load_weights('modelskeleton8.h5')
loadedModel.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

In [ ]:
features = inputProcessing("B:\PESU Labs\Capstone\ISL Translation\Demo\WhatsApp Video 2022-12-01 at 5.13.05 PM.mp4")
output = loadedModel.predict(features)
label = classList[np.argmax(output)]
print(label)